In [1]:
from docplex.mp.model import Model
mdl = Model(name="busLG")

In [2]:
import pandas as pd
import numpy as np

In [4]:
distance_adj_matrix_df= pd.read_excel('cplex/distance_adj_matrix_df_cplex.xlsx')
time_adj_matrix_df= pd.read_excel('cplex/time_adj_matrix_df_cplex.xlsx')
student_df_agg= pd.read_excel('cplex/student_df_agg_cplex.xlsx')

In [5]:
adj_ind=time_adj_matrix_df.id.values.tolist()

In [6]:
#FIXED!!!!: the depot also needs to be included in the matrix
t=pd.DataFrame(time_adj_matrix_df.iloc[:,1:77]) #preparing the matrix t (time adj)
t=t.transpose()
t.index = [adj_ind]
t.columns =[adj_ind]

In [7]:
d=pd.DataFrame(distance_adj_matrix_df.iloc[:,1:77]) #preparing the matrix d (distance adj)
d=d.transpose()
d.columns =[adj_ind]
d.index = [adj_ind]

In [8]:
#uncomplicated sets
N=student_df_agg.iloc[:,0].values.tolist()
B=[5600,5601,5606,5607,5651,5700,5701,5702,5703,5704,5705,5706,5707,5708,5709,5751,5752,5753] #18buses
L=time_adj_matrix_df.id.values.tolist() 
S = student_df_agg['school_name'].unique().tolist()
L_=L[1:]

In [10]:
student_school_np = pd.read_excel('cplex/student_school_np.xlsx')
s_n=pd.DataFrame(student_school_np.iloc[:,0:26])
s_n.columns =[S]
s_n.index = N

In [11]:
s_n

BBS I BBS II BBS III FöS G AM Knieberg FöS G am Knieberg Kooperation  \
1       1      0       0                 0                             0   
2       1      0       0                 0                             0   
3       1      0       0                 0                             0   
4       1      0       0                 0                             0   
5       1      0       0                 0                             0   
..    ...    ...     ...               ...                           ...   
230     0      0       0                 0                             0   
231     0      0       0                 0                             0   
232     0      0       0                 0                             0   
233     0      0       0                 0                             0   
234     0      0       0                 0                             0   

    FöS Johannes-Rabeler-Schule GS Amelinghausen GS Betzendorf  \
1                             0                0             0   
2                             0                0             0   
3                             0                0             0   
4                             0                0             0   
5                             0                0             0   
..                          ...              ...           ...   
230                           0                0             0   
231                           0                0             0   
232                           0                0             0   
233                           0                0             0   
234                           0                0             0   

    GS Deutsch Evern GS Embsen  ... Gym Salzhausen Gym Wilhelm-Raabe-Schule  \
1                  0         0  ...              0                        0   
2                  0         0  ...              0                        0   
3                  0         0  ...              0                        0   
4                  0         0  ...              0                        0   
5                  0         0  ...              0                        0   
..               ...       ...  ...            ...                      ...   
230                0         0  ...              0                        0   
231                0         0  ...              0                        0   
232                0         0  ...              0                        0   
233                0         0  ...              0                        0   
234                0         0  ...              0                        0   

    IGS Kreideberg IGS Lüneburg Oberschule Am Wasserturm  \
1                0            0                        0   
2                0            0                        0   
3                0            0                        0   
4                0            0                        0   
5                0            0                        0   
..             ...          ...                      ...   
230              0            0                        0   
231              0            0                        0   
232              0            0                        0   
233              0            0                        0   
234              0            0                        0   

    Oberschule Christiani Oberschule Oedeme Oberschule Salzhausen  \
1                       0                 0                     0   
2                       0                 0                     0   
3                       0                 0                     0   
4                       0                 0                     0   
5                       0                 0                     0   
..                    ...               ...                   ...   
230                     0                 0                     0   
231                     0                 0                     0   
232    

In [12]:
#I_s
I_s = pd.read_excel('cplex/I_s.xlsx') # NEW!!! now it is an excel file
I_s.index = [S]

In [13]:
I_s.columns

Int64Index([ 92501,  92505,  92301,  91701,  91902,  91901,  92901,  93601,
             93001,  92702,  92508,  91602,  91803,  92002,  92003,  92201,
             92503,  90601,  90606,  90605,  90701,  90904,  90903,  90905,
            550551,  90802,  90801,  90301,  92203,  90501,  91401,  92504,
             91603,  91502,  60605,  51303,  51310,  51309,  51308,  51305,
             51314,  90302,  51302,  90309,  90308,  90305,  90602,  90607,
            150095,  50024, 250080, 250003, 150087,  93101,  93102,  93201,
            150084, 150065, 250079, 250051, 150089,  92601,  92603,  92103,
             92302,  96409,  96601,  50089,  91501, 150097,  89121, 250005,
            150098,  50076, 250095],
           dtype='int64')

In [14]:
np.transpose(s_n).columns

Int64Index([  1,   2,   3,   4,   5,   6,   7,   8,   9,  10,
            ...
            225, 226, 227, 228, 229, 230, 231, 232, 233, 234],
           dtype='int64', length=234)

In [15]:
#FIXED???: too many Bus stops in here in comparison to L_ & L... now L_ is all bus stops as we agreed (both pickup and school)
I_s_n=s_n.dot(I_s)
I_s_n = np.transpose(I_s_n)

In [16]:
I_s_n.columns

Int64Index([  1,   2,   3,   4,   5,   6,   7,   8,   9,  10,
            ...
            225, 226, 227, 228, 229, 230, 231, 232, 233, 234],
           dtype='int64', length=234)

In [17]:
print(type(I_s_n[1]))

<class 'pandas.core.series.Series'>


In [45]:
school_max_transfers_np = pd.read_excel('cplex/school_max_transfers_np.xlsx')
school_max_transfers_np.index = [S]
print(school_max_transfers_np)

                               0  2
BBS I                          0  1
BBS II                         0  1
BBS III                        0  1
FöS G AM Knieberg              0  1
FöS G am Knieberg Kooperation  0  1
FöS Johannes-Rabeler-Schule    0  1
GS Amelinghausen               1  0
GS Betzendorf                  1  0
GS Deutsch Evern               1  0
GS Embsen                      1  0
GS Hermann Löns                1  0
GS Melbeck                     1  0
GS Rudolf-Steiner-Schule       1  0
GS Soderstorf                  1  0
GS St. Ursula                  1  0
Gym Johanneum                  0  1
Gym Salzhausen                 0  1
Gym Wilhelm-Raabe-Schule       0  1
IGS Kreideberg                 0  1
IGS Lüneburg                   0  1
Oberschule Am Wasserturm       0  1
Oberschule Christiani          0  1
Oberschule Oedeme              0  1
Oberschule Salzhausen          0  1
Rudolf-Steiner-Schule          0  1
Sonstige                       0  1


In [19]:
#l_s_n
l_s_n=s_n.dot(school_max_transfers_np)
l_s_n = np.transpose(l_s_n)

In [20]:
l_s_n.columns

Int64Index([  1,   2,   3,   4,   5,   6,   7,   8,   9,  10,
            ...
            225, 226, 227, 228, 229, 230, 231, 232, 233, 234],
           dtype='int64', length=234)

PARAMETERS: With dataframes (using indeces)

In [21]:
#18buses all the same type: big bus 
Bus=((B[0],1,81,0.003), 
     (B[1],1,81,0.003),
     (B[2],1,81,0.003),
     (B[3],1,81,0.003),
     (B[4],1,81,0.003),
     (B[5],1,81,0.003),
     (B[6],1,81,0.003),
     (B[7],1,81,0.003),
     (B[8],1,81,0.003),
     (B[9],1,81,0.003),
     (B[10],1,81,0.003),
     (B[11],1,81,0.003),
     (B[12],1,81,0.003),
     (B[13],1,81,0.003),
     (B[14],1,81,0.003),
     (B[15],1,81,0.003),
     (B[16],1,81,0.003),
     (B[17],1,81,0.003)
     )

In [22]:
Bus2=pd.DataFrame(Bus) #turning bus related parameters into dataframe
Bus2=Bus2.set_index(0)

In [23]:
c_b=Bus2.drop(Bus2.columns[[0,2]], axis=1) #bus related cost parameters with bus line as index
c_b= np.transpose(c_b)
q_b=Bus2.drop(Bus2.columns[[0,1]], axis=1)
q_fix = 40/60
gamma_up=15 
gamma_low=5

In [ ]:
Bus2

In [ ]:
c_b

In [ ]:
q_b

In [ ]:
# Sch2 was not done because it was used in the cell that was not used 

In [25]:
w_up_sch_s = pd.read_excel('cplex/school_wait_up.xlsx')
w_up_sch_s.index=[S]
w_low_sch_s = pd.read_excel('cplex/school_wait_low.xlsx')
w_low_sch_s.index=[S]

In [26]:
tau_sch_s=pd.read_excel('cplex/tau_sch_s.xlsx')
tau_sch_s.index=[S]


In [ ]:
tau_sch_s.columns

In [ ]:
w_up_sch_s

In [ ]:
w_low_sch_s

In [27]:
w_up=s_n.dot(w_up_sch_s)
w_up=np.transpose(w_up)
w_low=s_n.dot(w_low_sch_s)
w_low=np.transpose(w_low)
tau_s=s_n.dot(tau_sch_s)
tau_s=np.transpose(tau_s)

In [ ]:
tau_s.columns

In [ ]:
w_low.columns

In [ ]:
w_up.columns

In [29]:
r_n = pd.read_excel('cplex/r_n.xlsx')
r_n.index= N
r_n = np.transpose(r_n)

In [ ]:
r_n.columns

In [30]:
max_tt_n =pd.read_excel('cplex/max_tt_n.xlsx') # max travel time 
max_tt_n.index= [S]

In [31]:
max_tt_n=s_n.dot(max_tt_n)

In [32]:
max_tt_n = np.transpose(max_tt_n)


In [ ]:
max_tt_n.columns

In [33]:
y_n = pd.read_excel('cplex/y_n.xlsx') # 75 columns
y_n.index = N     
y_n = np.transpose(y_n)

In [ ]:
y_n.columns

In [ ]:
# BINARY VARIABLES (only execute once!)

In [38]:
X = [(i,j,b) for i in L for j in L for b in B if i != j]
x = mdl.binary_var_dict(X, name='x')

In [39]:
V_1 = [(i_1, b_1, b_2) for i_1 in L for b_1 in B for b_2 in B if b_1 != b_2]
v = mdl.binary_var_dict(V_1, name='v')

In [40]:
M = [(n, i, j, b) for n in N for i in L for j in L for b in B if i != j]
m = mdl.binary_var_dict(M, name='m')

In [41]:
Z = [(n, b, i) for n in N for b in B for i in L]
z = mdl.binary_var_dict(Z, name='z')

In [42]:
# CONTINUOS VARIABLES
V_2=[(i,b) for i in L for b in B]  #every stop for every bus
T_in = [(n,i) for n in N for i in L]

#arrival time of bus b at bus stop i
A=mdl.continuous_var_dict(V_2, ub=None, name='a') 

#arrival time of pupil n at bus stop i
T=mdl.continuous_var_dict(T_in, ub=None, name='t') 

In [36]:
#adjustable parameters
beta = 0.5
M_transfer = 10000

In [35]:
print(int(np.array(tau_s[43].index[tau_s[43] == 1])))
print(int(np.array(w_up[43].index[w_up[43] == 1])))
print(I_s_n[45].index[I_s_n[45]==1].tolist())

480
30
[92501, 92504]


In [ ]:
#cost function, check
mdl.minimize((1-beta)*mdl.sum(x[i,j,b]*int(np.array(t[[i]].loc[[j]]))*q_fix + int(np.array(d[[i]].loc[[j]]))*x[i,j,b]*float(np.array(q_b.loc[[b]]))
                              for i in L_
                              for j in L_ if i!=j
                              for b in B) 
             +(beta)*(0.1)*mdl.sum(m[n,i,j,b]*int(np.array(t[[i]].loc[[j]]))*int(np.array(r_n[n])) 
                             for i in L_
                             for j in L_ if i!=j
                             for b in B
                             for n in N))
                         

In [43]:
#A bus line must have a single origin at the virtual depot if the bus is used, check
#mdl.add_constraints(x[0,i,b]>=mdl.sum(x[i,j,b] for j in L_ if j!=i)-mdl.sum(x[k,i,b] for k in L_ if k!=i) for b in B for i in L_)
mdl.add_constraints(mdl.sum(x[0,i,b]for i in L_) <=1 for b in B)

[docplex.mp.LinearConstraint[](x_0_92501_5600+x_0_92505_5600+x_0_92301_5600+x_0_91701_5600+x_0_91902_5600+x_0_91901_5600+x_0_92901_5600+x_0_93601_5600+x_0_93001_5600+x_0_92702_5600+x_0_92508_5600+x_0_91602_5600+x_0_91803_5600+x_0_92002_5600+x_0_92003_5600+x_0_92201_5600+x_0_92503_5600+x_0_90601_5600+x_0_90606_5600+x_0_90605_5600+x_0_90701_5600+x_0_90904_5600+x_0_90903_5600+x_0_90905_5600+x_0_550551_5600+x_0_90802_5600+x_0_90801_5600+x_0_90301_5600+x_0_92203_5600+x_0_90501_5600+x_0_91401_5600+x_0_92504_5600+x_0_91603_5600+x_0_91502_5600+x_0_60605_5600+x_0_51303_5600+x_0_51310_5600+x_0_51309_5600+x_0_51308_5600+x_0_51305_5600+x_0_51314_5600+x_0_90302_5600+x_0_51302_5600+x_0_90309_5600+x_0_90308_5600+x_0_90305_5600+x_0_90602_5600+x_0_90607_5600+x_0_150095_5600+x_0_50024_5600+x_0_250080_5600+x_0_250003_5600+x_0_150087_5600+x_0_93101_5600+x_0_93102_5600+x_0_93201_5600+x_0_150084_5600+x_0_150065_5600+x_0_250079_5600+x_0_250051_5600+x_0_150089_5600+x_0_92601_5600+x_0_92603_5600+x_0_92103_5600

In [44]:
#no cycles
#mdl.add_constraints(mdl.sum(x[j,i,b] for j in L_ if i!=j)+mdl.sum(x[i,j,b] for j in L_ if i!=j)<=1 for b in B for i in L_)

#must return to virtual depot
mdl.add_constraints(mdl.sum(x[j,i,b] for j in L if i!=j)-mdl.sum(x[i,j,b] for j in L if i!=j)==0 for b in B for i in L_)

[docplex.mp.LinearConstraint[](x_0_92501_5600-x_92501_0_5600-x_92501_92505_5600-x_92501_92301_5600-x_92501_91701_5600-x_92501_91902_5600-x_92501_91901_5600-x_92501_92901_5600-x_92501_93601_5600-x_92501_93001_5600-x_92501_92702_5600-x_92501_92508_5600-x_92501_91602_5600-x_92501_91803_5600-x_92501_92002_5600-x_92501_92003_5600-x_92501_92201_5600-x_92501_92503_5600-x_92501_90601_5600-x_92501_90606_5600-x_92501_90605_5600-x_92501_90701_5600-x_92501_90904_5600-x_92501_90903_5600-x_92501_90905_5600-x_92501_550551_5600-x_92501_90802_5600-x_92501_90801_5600-x_92501_90301_5600-x_92501_92203_5600-x_92501_90501_5600-x_92501_91401_5600-x_92501_92504_5600-x_92501_91603_5600-x_92501_91502_5600-x_92501_60605_5600-x_92501_51303_5600-x_92501_51310_5600-x_92501_51309_5600-x_92501_51308_5600-x_92501_51305_5600-x_92501_51314_5600-x_92501_90302_5600-x_92501_51302_5600-x_92501_90309_5600-x_92501_90308_5600-x_92501_90305_5600-x_92501_90602_5600-x_92501_90607_5600-x_92501_150095_5600-x_92501_50024_5600-x_9250

In [46]:
#Every bus line may service each bus stop only once, check
mdl.add_constraints(mdl.sum(x[i,j,b] for j in L_ if i!=j) <= 1 
                    for b in B
                    for i in L)

[docplex.mp.LinearConstraint[](x_0_92501_5600+x_0_92505_5600+x_0_92301_5600+x_0_91701_5600+x_0_91902_5600+x_0_91901_5600+x_0_92901_5600+x_0_93601_5600+x_0_93001_5600+x_0_92702_5600+x_0_92508_5600+x_0_91602_5600+x_0_91803_5600+x_0_92002_5600+x_0_92003_5600+x_0_92201_5600+x_0_92503_5600+x_0_90601_5600+x_0_90606_5600+x_0_90605_5600+x_0_90701_5600+x_0_90904_5600+x_0_90903_5600+x_0_90905_5600+x_0_550551_5600+x_0_90802_5600+x_0_90801_5600+x_0_90301_5600+x_0_92203_5600+x_0_90501_5600+x_0_91401_5600+x_0_92504_5600+x_0_91603_5600+x_0_91502_5600+x_0_60605_5600+x_0_51303_5600+x_0_51310_5600+x_0_51309_5600+x_0_51308_5600+x_0_51305_5600+x_0_51314_5600+x_0_90302_5600+x_0_51302_5600+x_0_90309_5600+x_0_90308_5600+x_0_90305_5600+x_0_90602_5600+x_0_90607_5600+x_0_150095_5600+x_0_50024_5600+x_0_250080_5600+x_0_250003_5600+x_0_150087_5600+x_0_93101_5600+x_0_93102_5600+x_0_93201_5600+x_0_150084_5600+x_0_150065_5600+x_0_250079_5600+x_0_250051_5600+x_0_150089_5600+x_0_92601_5600+x_0_92603_5600+x_0_92103_5600

In [47]:
#Students can only use existing bus lines, check
mdl.add_constraints(m[n,i,j,b] <= x[i,j,b]
                    for i in L_
                    for j in L_ if i != j
                    for b in B
                    for n in N)

KeyboardInterrupt: 

In [ ]:
#If pupil n is assigned to bus stop i (yni = 1) which is not her destination bus stop i = isn she must leave the pickup busstop

mdl.add_constraints(y_n[n].loc[i] <= mdl.sum(m[n,i,j,b]for j in L_ if j!=i for b in B)
                    for n in N for i in y_n[n].index[y_n[n]==1].tolist() if i in I_s_n[n].index[I_s_n[n]==0].tolist())

In [ ]:
#if pupil n arrives at bus stop and it is not her destination bus stop, she must travel on to another bus stop 

mdl.add_constraints(mdl.sum(m[n,i,h,b]for i in L_ if h!=i for b in B)<=mdl.sum(m[n,h,j,b]for j in L_ if h!=j for b in B)
                    for n in N for h in I_s_n[n].index[I_s_n[n]==0].tolist())

In [ ]:
#Every student (or sets of pupils) n ∈ N must arrive at exactly one bus stop for their destination school
#mdl.add_constraints(mdl.sum(m[n,j,i,b] 
                            #for b in B 
                            #for i in I_s_n[n].index[I_s_n[n]==1].tolist()
                            #for j in L_ if i!=j) == 1 for n in N)

In [ ]:
#A student can leave a bus stop only once, check
mdl.add_constraints(mdl.sum(m[n,i,j,b] 
                            for j in L_ if j!=i
                            for b in B ) <= 1 
                    for i in L_
                    for n in N)

In [ ]:
#feasible transfers, check
mdl.add_constraints(mdl.sum(m[n,j,i,b] for j in L_ if j!=i) - mdl.sum(m[n,i,j,b] for j in L_ if j!=i) <= z[n,b,i]  
                    for i in L_
                    for n in N
                    for b in B)

#mdl.add_constraints(mdl.sum(m[n,j,i,b]  for i in L_ for j in L_ if j!=i) >= mdl.sum(z[n,b,i]  for i in L_)
                    #for n in N
                    #for b in B)

In [ ]:
#Each pupil may only leave each bus b at most once, check
mdl.add_constraints(mdl.sum(z[n,b,i] for i in L_)<=1 
                    for b in B
                    for n in N)

In [ ]:
print(I_s_n[43].index[I_s_n[43]==0])

In [ ]:
#Each student (or sets of students) n does not exceed the transfer limit of their school sn, check
mdl.add_constraints(mdl.sum(z[n,b,i] 
                            for b in B
                            for i in L_ if i in I_s_n[n].index[I_s_n[n]==0].tolist())<= int(np.array(l_s_n[n].index[l_s_n[n]==1].tolist())) for n in N)
mdl.add_constraints(mdl.sum(z[n,b,i] 
                            for b in B
                            for i in L_ if i in I_s_n[n].index[I_s_n[n]==1].tolist())== 1 for n in N)

            

In [ ]:
#definition of v[j,b'b''], check
mdl.add_constraints(mdl.sum(m[n,i,j,b_1] for i in L_ if i!=j) + mdl.sum(m[n,j,k,b_2] for k in L_ if k!=j) <= (v[j,b_1,b_2]+1) 
                    for n in N
                    for j in L_
                    for b_1 in B
                    for b_2 in B if b_1 != b_2)

mdl.add_constraints(v[j,b_1,b_2] + v[j,b_2,b_1] <= 1 
                    for j in L_
                    for b_1 in B
                    for b_2 in B if b_1 != b_2)                    

In [ ]:
#If pupil n travels from i to j then her arrival time at j must be greater or equal to the arrival time at i plus the time needed to travel from i to j (tij), check
mdl.add_constraints((T[n,i] + int(np.array(t[[i]].loc[[j]])) - M_transfer*(1-mdl.sum(m[n,i,j,b] for b in B))) <= T[n,j]
                    for i in L_
                    for j in L_ if j!=i
                    for n in N)

In [ ]:
print(int(np.array(t[[51309]].loc[[51314]])))

In [ ]:
#Pupil n must arrive at one bus stop for her destination school within the school’s arrival time

mdl.add_indicator_constraints(mdl.indicator_constraint(m[n,j,i,b], int(np.array(tau_s[n].index[tau_s[n] == 1])) - int(np.array(w_up[n].index[w_up[n] == 1]))<= T[n,i]) for n in N  for i in I_s_n[n].index[I_s_n[n]==1].tolist() for j in L_ if j!=i for b in B)
mdl.add_indicator_constraints(mdl.indicator_constraint(m[n,j,i,b], int(np.array(tau_s[n].index[tau_s[n] == 1])) - int(np.array(w_up[n].index[w_low[n] == 1]))>= T[n,i]) for n in N  for i in I_s_n[n].index[I_s_n[n]==1].tolist() for j in L_ if j!=i for b in B)

In [ ]:
#If bus b travels from i to j then arrival time at j must be equal to travel time at i plus travel time from i to j
mdl.add_constraints(A[j,b]<=A[i,b]+int(np.array(t[[i]].loc[[j]]))+M_transfer*(1-x[i,j,b]) 
                    for i in L
                    for j in L_ if i!=j
                    for b in B)
mdl.add_constraints(A[j,b]>=A[i,b]+int(np.array(t[[i]].loc[[j]]))-M_transfer*(1-x[i,j,b]) 
                    for i in L
                    for j in L_ if i!=j
                    for b in B)

In [ ]:
#If pupil n travels on bus b her arrival time at stop i has to be the same as of bus b
#check
mdl.add_constraints(T[n,i]>=A[i,b]-M_transfer*(1-mdl.sum(m[n,j,i,b] for j in L if j!=i)) 
                    for i in L
                    for n in N
                    for b in B)
mdl.add_constraints(T[n,i]<=A[i,b]+M_transfer*(1-mdl.sum(m[n,j,i,b] for j in L if j!=i)) 
                    for i in L
                    for n in N
                    for b in B)

In [ ]:
#If pupil n changes from b’ to b” at stop i then the arrival time of b” can’t be greater than of b’ plus max waiting time y and not lower than arrival time of b’ plus min waiting time y
#check
mdl.add_constraints((A[i,b_1]+gamma_up+M_transfer*(1-v[i,b_1,b_2])) >= A[i,b_2]
                    for i in L
                    for n in N
                    for b_1 in B
                    for b_2 in B if b_1!=b_2)
mdl.add_constraints(A[i,b_2]>= (A[i,b_1]+gamma_low-M_transfer*(1-v[i,b_1,b_2])) 
                    for i in L
                    for n in N
                    for b_1 in B
                    for b_2 in B if b_1!=b_2)

In [ ]:
# capacity constraint
mdl.add_constraints(mdl.sum(m[n,i,j,b]*int(np.array(r_n[n])) 
                            for j in L_ if j!= i
                            for n in N ) <= int(np.array(c_b[b]))
                    for i in L_ 
                    for b in B)

                    

In [ ]:
#OPTIONAL: to run parallely with and without this constraint -> max_tt needs to be creared

mdl.add_constraints(mdl.sum(m[n,i,j,b]*int(np.array(t[[i]].loc[[j]]))
                             for i in L_
                             for j in L_ if i!=j
                             for b in B)<= int(np.array(max_tt[n].index[max_tt[n] == 1])) for n in N)

In [ ]:
from docplex.mp.conflict_refiner import ConflictRefiner

cr = ConflictRefiner()
crr = cr.refine_conflict(mdl, display=True)
cr.display_conflicts(crr)

In [ ]:
#mdl.parameters.emphasis.mip = 1

In [ ]:
solution=mdl.solve(log_output=True)

In [ ]:
print(solution)


In [ ]:
type(solution)

with open("solution.txt", "w") as solfile:
    solfile.write(mdl.solution.to_string())